In [1]:
import pandas as pd
import numpy as np

import plotly.express as px

In [2]:
from sklearn.linear_model import LogisticRegressionCV, LogisticRegression
from sklearn.svm import SVC, LinearSVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from xgboost import XGBClassifier
from sklearn.neighbors import KNeighborsClassifier

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.pipeline import Pipeline
from sklearn.metrics import confusion_matrix, roc_auc_score, f1_score, classification_report

In [3]:
import functions

In [10]:
imdb_df = pd.read_csv('data/imdb_clean.csv')

## Data Preparation

In [11]:
imdb_df.columns

Index(['actor1', 'actor2', 'actor3', 'actor4', 'director', 'Action', 'Adult',
       'Adventure', 'Animation', 'Biography', 'Comedy', 'Crime', 'Documentary',
       'Drama', 'Family', 'Fantasy', 'Film-Noir', 'Game-Show', 'History',
       'Horror', 'Music', 'Musical', 'Mystery', 'News', 'Reality-TV',
       'Romance', 'Sci-Fi', 'Short', 'Sport', 'Talk-Show', 'Thriller',
       'Unknown', 'War', 'Western', 'duration', 'imdb_rating', 'votes',
       'release_start', 'release_month', 'tv_series', 'title', 'synopsis'],
      dtype='object')

In [12]:
imdb_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 277967 entries, 0 to 277966
Data columns (total 42 columns):
 #   Column         Non-Null Count   Dtype  
---  ------         --------------   -----  
 0   actor1         277967 non-null  int64  
 1   actor2         277967 non-null  int64  
 2   actor3         277967 non-null  int64  
 3   actor4         277967 non-null  int64  
 4   director       277967 non-null  int64  
 5   Action         277967 non-null  int64  
 6   Adult          277967 non-null  int64  
 7   Adventure      277967 non-null  int64  
 8   Animation      277967 non-null  int64  
 9   Biography      277967 non-null  int64  
 10  Comedy         277967 non-null  int64  
 11  Crime          277967 non-null  int64  
 12  Documentary    277967 non-null  int64  
 13  Drama          277967 non-null  int64  
 14  Family         277967 non-null  int64  
 15  Fantasy        277967 non-null  int64  
 16  Film-Noir      277967 non-null  int64  
 17  Game-Show      277967 non-nul

In [13]:
model_df = imdb_df.drop(['title', 'synopsis'], axis=1).dropna()

In [14]:
model_df.shape

(183969, 40)

In [15]:
px.histogram(model_df, 'imdb_rating')

Binning the countinous variable into groups to be able to achieve classification tasks.

In [16]:
model_df['imdb_rating_cat'] = pd.cut(model_df['imdb_rating'], bins=[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10], right=True, labels=False) 
px.histogram(model_df, 'imdb_rating', color = 'imdb_rating_cat')

In [17]:
dep_var = f'imdb_rating_cat'
indep_vars = model_df.columns.drop(['imdb_rating', 'imdb_rating_cat'])

In [18]:
X = model_df[indep_vars]
y = model_df[dep_var]

In [19]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [20]:
X_train.shape, X_test.shape

((147175, 39), (36794, 39))

## Model training

In [21]:
model = LogisticRegression(max_iter=1000).fit(X_train, y_train)
model.score(X_test, y_test)

/home/hem/anaconda3/lib/python3.9/site-packages/sklearn/linear_model/_logistic.py:763: ConvergenceWarning:

lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression



0.3224438767190303

In [22]:
print(classification_report(y_test, model.predict(X_test)))

/home/hem/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

/home/hem/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.



              precision    recall  f1-score   support

           0       0.00      0.00      0.00         6
           1       0.00      0.00      0.00       108
           2       0.00      0.00      0.00       568
           3       0.00      0.00      0.00      1714
           4       0.00      0.00      0.00      4094
           5       0.27      0.01      0.02      8205
           6       0.32      0.98      0.48     11796
           7       0.41      0.03      0.05      7907
           8       0.75      0.01      0.01      2178
           9       0.00      0.00      0.00       218

    accuracy                           0.32     36794
   macro avg       0.18      0.10      0.06     36794
weighted avg       0.30      0.32      0.17     36794



/home/hem/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.



In [23]:
roc_auc_score(y_test, model.predict_proba(X_test), multi_class = 'ovr')

0.5607891772455698

In [24]:
f1_score(y_test, model.predict(X_test), average=None)

array([0.        , 0.        , 0.        , 0.        , 0.        ,
       0.02108716, 0.48379523, 0.05210801, 0.01364877, 0.        ])

In [25]:
xgb_model = XGBClassifier().fit(X_train, y_train)

In [26]:
xgb_model.score(X_test, y_test)

0.4083546230363646

In [27]:
roc_auc_score(y_test, xgb_model.predict_proba(X_test), multi_class = 'ovr')

0.7905241628071449

In [28]:
from hyperopt import STATUS_OK, Trials, fmin, hp, tpe
from sklearn.metrics import accuracy_score
# hyperparameter tuning for XGB
space={'max_depth': hp.quniform("max_depth", 3, 18, 1),
        'gamma': hp.uniform ('gamma', 1,9),
        'reg_alpha' : hp.quniform('reg_alpha', 40,180,1),
        'reg_lambda' : hp.uniform('reg_lambda', 0,1),
        'colsample_bytree' : hp.uniform('colsample_bytree', 0.5,1),
        'min_child_weight' : hp.quniform('min_child_weight', 0, 10, 1),
        'n_estimators': 180,
        'seed': 0
    }

In [29]:
def objective(space):
    clf=XGBClassifier(
                    n_estimators =space['n_estimators'], max_depth = int(space['max_depth']), gamma = space['gamma'],
                    reg_alpha = int(space['reg_alpha']),min_child_weight=int(space['min_child_weight']),
                    colsample_bytree=int(space['colsample_bytree']))
    
    evaluation = [( X_train, y_train), ( X_test, y_test)]
    
    clf.fit(X_train, y_train,
            eval_set=evaluation, eval_metric="auc",
            early_stopping_rounds=10,verbose=True)
    

    pred = clf.predict(X_test)
    accuracy = accuracy_score(y_test, pred>0.5)
    print ("SCORE:", accuracy)
    return {'loss': -accuracy, 'status': STATUS_OK }

In [30]:
trials = Trials()

best_hyperparams = fmin(fn = objective,
                        space = space,
                        algo = tpe.suggest,
                        max_evals = 100,
                        trials = trials)

  0%|          | 0/100 [00:00<?, ?trial/s, best loss=?]

/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.


/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.




[0]	validation_0-auc:0.51396	validation_1-auc:0.51293  
[1]	validation_0-auc:0.52923	validation_1-auc:0.52656  
[2]	validation_0-auc:0.53034	validation_1-auc:0.52736  
[3]	validation_0-auc:0.55555	validation_1-auc:0.55211  
[4]	validation_0-auc:0.55712	validation_1-auc:0.55303  
[5]	validation_0-auc:0.56023	validation_1-auc:0.55518  
[6]	validation_0-auc:0.56343	validation_1-auc:0.55843  
[7]	validation_0-auc:0.57613	validation_1-auc:0.57223  
[8]	validation_0-auc:0.57609	validation_1-auc:0.57231  
[9]	validation_0-auc:0.58096	validation_1-auc:0.57503  
[10]	validation_0-auc:0.60061	validation_1-auc:0.59577 
[11]	validation_0-auc:0.60370	validation_1-auc:0.59869 
[12]	validation_0-auc:0.61344	validation_1-auc:0.60861 
[13]	validation_0-auc:0.61548	validation_1-auc:0.61083 
[14]	validation_0-auc:0.61873	validation_1-auc:0.61376 
[15]	validation_0-auc:0.62618	validation_1-auc:0.62119 
[16]	validation_0-auc:0.62641	validation_1-auc:0.62139 
[17]	validation_0-auc:0.62701	validation_1-auc:0

/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.


/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.




[0]	validation_0-auc:0.50487	validation_1-auc:0.50411                                  
[1]	validation_0-auc:0.52371	validation_1-auc:0.52072                                  
[2]	validation_0-auc:0.52385	validation_1-auc:0.52082                                  
[3]	validation_0-auc:0.55223	validation_1-auc:0.54853                                  
[4]	validation_0-auc:0.55352	validation_1-auc:0.54955                                  
[5]	validation_0-auc:0.55731	validation_1-auc:0.55237                                  
[6]	validation_0-auc:0.56007	validation_1-auc:0.55525                                  
[7]	validation_0-auc:0.57233	validation_1-auc:0.56905                                  
[8]	validation_0-auc:0.57248	validation_1-auc:0.56923                                  
[9]	validation_0-auc:0.57720	validation_1-auc:0.57144                                  
[10]	validation_0-auc:0.59627	validation_1-auc:0.59111                                 
[11]	validation_0-auc:0.59927	va

...

[0]	validation_0-auc:0.50040	validation_1-auc:0.50059                                 
[1]	validation_0-auc:0.52170	validation_1-auc:0.51923                                 
[2]	validation_0-auc:0.52189	validation_1-auc:0.51931                                 
[3]	validation_0-auc:0.54721	validation_1-auc:0.54401                                 
[4]	validation_0-auc:0.54854	validation_1-auc:0.54504                                 
[5]	validation_0-auc:0.55099	validation_1-auc:0.54729                                 
[6]	validation_0-auc:0.55412	validation_1-auc:0.55061                                 
[7]	validation_0-auc:0.56735	validation_1-auc:0.56513                                 
[8]	validation_0-auc:0.56759	validation_1-auc:0.56544                                 
[9]	validation_0-auc:0.57419	validation_1-auc:0.56964                                 
[10]	validation_0-auc:0.59410	validation_1-auc:0.59035                                
[11]	validation_0-auc:0.59685	validation_1-

/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.


/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.




[0]	validation_0-auc:0.50040	validation_1-auc:0.50059                                 
[1]	validation_0-auc:0.52170	validation_1-auc:0.51923                                 
[2]	validation_0-auc:0.52190	validation_1-auc:0.51931                                 
[3]	validation_0-auc:0.54719	validation_1-auc:0.54396                                 
[4]	validation_0-auc:0.54861	validation_1-auc:0.54510                                 
[5]	validation_0-auc:0.55277	validation_1-auc:0.54832                                 
[6]	validation_0-auc:0.55575	validation_1-auc:0.55147                                 
[7]	validation_0-auc:0.56883	validation_1-auc:0.56616                                 
[8]	validation_0-auc:0.56907	validation_1-auc:0.56635                                 
[9]	validation_0-auc:0.57609	validation_1-auc:0.57054                                 
[10]	validation_0-auc:0.59597	validation_1-auc:0.59103                                
[11]	validation_0-auc:0.59887	validation_1-

/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`eval_metric` in `fit` method is deprecated for better compatibility with scikit-learn, use `eval_metric` in constructor or`set_params` instead.


/home/hem/anaconda3/lib/python3.9/site-packages/xgboost/sklearn.py:793: UserWarning:

`early_stopping_rounds` in `fit` method is deprecated for better compatibility with scikit-learn, use `early_stopping_rounds` in constructor or`set_params` instead.




[0]	validation_0-auc:0.50040	validation_1-auc:0.50059                                 
[1]	validation_0-auc:0.52170	validation_1-auc:0.51923                                 
[2]	validation_0-auc:0.52202	validation_1-auc:0.51948                                 
[3]	validation_0-auc:0.54710	validation_1-auc:0.54398                                 
[4]	validation_0-auc:0.54844	validation_1-auc:0.54499                                 
[5]	validation_0-auc:0.55085	validation_1-auc:0.54717                                 
[6]	validation_0-auc:0.55400	validation_1-auc:0.55049                                 
[7]	validation_0-auc:0.56724	validation_1-auc:0.56508                                 
[8]	validation_0-auc:0.56759	validation_1-auc:0.56547                                 
[9]	validation_0-auc:0.57424	validation_1-auc:0.56959                                 
[10]	validation_0-auc:0.59431	validation_1-auc:0.59037                                
[11]	validation_0-auc:0.59726	validation_1-

In [ ]:
best_hyperparams

{'colsample_bytree': 0.9567664873464423,
 'gamma': 6.0433502077661,
 'max_depth': 14.0,
 'min_child_weight': 5.0,
 'reg_alpha': 56.0,
 'reg_lambda': 0.355670978581757}

In [34]:
xgb_mod = XGBClassifier(colsample_bytree = 0.9567664873464423,
                        gamma = 6.0433502077661,
                        max_depth = 14,
                        min_child_weight = 5,
                        reg_alpha = 56.0,
                        reg_lambda = 0.355670978581757).fit(X_train, y_train)
xgb_mod.score(X_test, y_test)

0.3944052104908542

In [35]:
print(classification_report(y_test, xgb_mod.predict(X_test)))

              precision    recall  f1-score   support

           0       0.00      0.00      0.00         2
           1       0.00      0.00      0.00       119
           2       0.14      0.00      0.00       571
           3       0.36      0.13      0.20      1893
           4       0.37      0.13      0.20      4486
           5       0.35      0.32      0.33      8896
           6       0.40      0.62      0.49     12902
           7       0.42      0.48      0.45      8562
           8       0.42      0.02      0.04      2424
           9       0.00      0.00      0.00       218

    accuracy                           0.39     40073
   macro avg       0.25      0.17      0.17     40073
weighted avg       0.38      0.39      0.36     40073



/home/hem/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

/home/hem/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.

/home/hem/anaconda3/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning:

Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.



In [36]:
roc_auc_score(y_test, xgb_mod.predict_proba(X_test), multi_class = 'ovr')

0.7772603186589705

## Naive Bayes on Synopsis

In [4]:
from sklearn.pipeline import make_pipeline
from sklearn.feature_extraction.text import TfidfVectorizer
from gensim.parsing.preprocessing import remove_stopwords
import re

In [14]:
imdb_df.columns

Index(['actors', 'director', 'duration', 'genre', 'imdb_rating', 'link',
       'synopsis', 'title', 'votes', 'page_url', 'page_url_cleaned',
       'release_start', 'action', 'adult', 'adventure', 'animation',
       'biography', 'comedy', 'crime', 'documentary', 'drama', 'family',
       'fantasy', 'film-noir', 'game-show', 'history', 'horror', 'music',
       'musical', 'mystery', 'news', 'reality-tv', 'romance', 'sci-fi',
       'short', 'sport', 'talk-show', 'thriller', 'unknown', 'war', 'western',
       'tv_series'],
      dtype='object')

In [69]:
text_df = imdb_df[['imdb_rating', 'synopsis']].dropna()
# Revome add plot
text_df = text_df[text_df['synopsis'] != 'Add a Plot'].dropna(subset=['synopsis']).reset_index(drop=True)
# Remove punctuation
text_df['synopsis'] = text_df['synopsis'].map(lambda x: re.sub('[!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~]', '', x))
# Convert the titles to lowercase
text_df['synopsis'] = text_df['synopsis'].map(lambda x: x.lower())
# Removing 'see full summary'
text_df['synopsis'] = text_df['synopsis'].map(lambda x: re.sub('see full summary\xa0»', '', x))
# Print out the first rows of papers
text_df['synopsis'] = text_df['synopsis'].str.strip()
# Remove stopwords
text_df['synopsis'] = [remove_stopwords(i) for i in text_df['synopsis']]

In [70]:
text_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 79840 entries, 0 to 79839
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   imdb_rating  79840 non-null  float64
 1   synopsis     79840 non-null  object 
dtypes: float64(1), object(1)
memory usage: 1.2+ MB


In [71]:
np.unique(np.array([str(type(i)) for i in text_df['synopsis']]))

array(["<class 'str'>"], dtype='<U13')

In [72]:
text_df['imdb_rating_cat'] = pd.cut(text_df['imdb_rating'], bins=[0, 2, 4, 5, 6, 7, 8, 10], right=True, labels=['0-2', '2-4', '4-5', '5-6', '6-7', '7-8', '8-10']) 

In [73]:
text_df.imdb_rating_cat.value_counts()

6-7     25714
7-8     18157
5-6     17268
4-5      8563
8-10     5413
2-4      4514
0-2       211
Name: imdb_rating_cat, dtype: int64

In [74]:
text_df_tmp = text_df.iloc[0:70000]

In [75]:
# Build the model
model = make_pipeline(TfidfVectorizer(), MultinomialNB())
# Train the model using the training data
model.fit(text_df['synopsis'], text_df['imdb_rating_cat'])
# Predict the categories of the test data
predicted_categories = model.predict(text_df['synopsis'])

In [76]:
model.score(text_df['synopsis'], text_df['imdb_rating_cat'])

0.4258892785571142